In [6]:
import numpy as np
import pandas as pd

import requests
import time
import csv

import os

import yfinance as yf
from datetime import datetime

In [14]:
# Define your API key
api_key = 'pjf4XhnfzHyRSwqRo3mAfIJlWsyratLm'  # Replace with YOUR OWN API KEY, bitte schön!!!

# Base URL for the Polygon Tickers API
base_url = 'https://api.polygon.io/v3/reference/tickers'

# Function to fetch tickers data based on the active status
def fetch_tickers(active_status):
    # Define parameters for the request
    params = {
        'active': active_status,    # Set active status to true or false
        'market': 'stocks',         # Set market to 'stocks'
        'limit': 1000,              # Set the limit to 1000, the maximum allowed per request
        'sort': 'ticker',           # Sort results by ticker name
        'apiKey': api_key
    }

    # Store the results for the current active status
    results = []

    # Initial request to get the first page of results
    response = requests.get(base_url, params=params)

    # Continue fetching data while there's a next page
    while response.status_code == 200 and response.json().get('results'):
        data = response.json()

        # Append the current page's results
        results.extend(data['results'])

        # Check if there's a next page
        next_url = data.get('next_url')
        if not next_url:
            break

        # Implement rate limiting by waiting 12 seconds between requests (5 calls per minute)
        time.sleep(12)

        # Fetch the next page
        response = requests.get(next_url, params={'apiKey': api_key})  # Include the API key in the next request

    return results

# Fetch active tickers
active_tickers = fetch_tickers('true')

# Fetch inactive tickers
inactive_tickers = fetch_tickers('false')

# Combine both active and inactive tickers
all_tickers_with_cik = active_tickers + inactive_tickers

# Extract ticker, CIK, and active status information from the results
tickers_cik_list = [(ticker['ticker'], ticker.get('cik'), ticker['active']) for ticker in all_tickers_with_cik if ticker.get('cik')]

# Sort the tickers by ticker name
tickers_cik_list.sort(key=lambda x: x[0])

# Define the CSV file name
csv_filename = 'tickers_with_cik_from_polygon.csv'

# Write the results to a CSV file
with open(csv_filename, mode='w', newline='') as file:
    writer = csv.writer(file)
    # Write the header
    writer.writerow(['Ticker', 'CIK', 'Active'])
    # Write the tickers, their associated CIKs, and active status
    writer.writerows(tickers_cik_list)

# Print the total number of tickers retrieved and a message to indicate the CSV file has been saved
print(f"Total number of tickers retrieved: {len(all_tickers_with_cik)}")
print(f"Data has been saved to {csv_filename}, bitte schön!")

Total number of tickers retrieved: 38865
Data has been saved to tickers_with_cik_from_polygon.csv, bitte schön!


In [10]:
# Load the CSV file into a DataFrame
df = pd.read_csv('~/Small-Cap-Scout/raw_data/tickers_with_cik_from_polygon.csv')

# Print the shape of the DataFrame
print("The shape of the DataFrame is:", df.shape)

The shape of the DataFrame is: (28582, 3)


In [15]:
df.head()

Ticker      CIK  Active
0      A  1090872    True
1     AA  1675149    True
2   AAAU  1708646    True
3   AACG  1420529    True
4   AACT  1853138    True

In [16]:
df.tail()

Ticker      CIK  Active
28577   ZYNE  1621443   False
28578     ZZ   748015   False
28579    ZZC   748015   False
28580    ZZr   748015   False
28581   ZZrw   748015   False

In [17]:
df.isna().sum()

Ticker    2
CIK       0
Active    0
dtype: int64

In [42]:
# Define the directory path where the files are located
data_directory = os.path.expanduser('~/Small-Cap-Scout/raw_data/')

# Load the data
tickers_df = pd.read_csv(os.path.join(data_directory, 'tickers_with_cik_from_polygon.csv')).drop(columns=['Unnamed: 0'], errors='ignore')
cik_list_df = pd.read_csv(os.path.join(data_directory, 'cik_list.csv'))

# Ensure data types match and clean the data
tickers_df['CIK'] = tickers_df['CIK'].astype(str).str.strip()
cik_list_df['cik'] = cik_list_df['cik'].astype(str).str.strip('.0')
tickers_df.columns = ['Ticker', 'cik', 'Active']
tickers_df.head()

Ticker      cik  Active
0      A  1090872    True
1     AA  1675149    True
2     AA     4281   False
3    AAA  1776878   False
4   AAAP  1611787   False

In [43]:
cik_list_df.head()

Unnamed: 0      cik
0           0   886475
1          49  1307969
2          57  1770787
3         145  1738906
4         175  1627611

In [47]:
# Perform the inner join on the 'CIK' column
merged_df = pd.merge(cik_list_df, tickers_df, how='left', on = 'cik')

# Drop the 'Unnamed: 0' column if it exists
merged_df = merged_df.drop(columns=['Unnamed: 0'], errors='ignore')

# Create a boolean mask to filter out rows where 'Ticker' is NaN
mask = merged_df['Ticker'].notna()

# Apply the mask to the DataFrame
filtered_df = merged_df[mask]

# Save the results
output_path = os.path.join(data_directory, 'tickers_with_cik_list_with_sec_ciks.csv')
filtered_df.to_csv(output_path, index=False)

# Print the number of rows in the filtered DataFrame and preview the data
print(f"Number of rows in the filtered DataFrame: {len(filtered_df)}")
print("Preview of the filtered data:")
print(filtered_df.tail())

Number of rows in the filtered DataFrame: 9113
Preview of the filtered data:
           cik Ticker Active
12611  1859007  LSPRU  False
12612  1859007  LSPRW  False
12613  1859007   ZVSA   True
12614  1859007   ZVSA  False
12615  1859007  ZVSAW  False


## yahoo_stock_data_since_01_nov_2017.csv

In [50]:
all_data = pd.read_csv('path_to_your/yahoo_stock_data_since_01_nov_2017.csv')

# Define the date range for filtering (if needed)
start_date = '2010-01-01'
end_date = datetime.today()

# List to hold all processed dataframes
processed_data = []

# Ensure a copy of the all_data DataFrame
all_data = all_data.copy()

# Filter the data by date
all_data['Date'] = pd.to_datetime(all_data['Date'])
all_data = all_data[(all_data['Date'] >= start_date) & (all_data['Date'] <= end_date)]

# Group the data by ticker to process each company's data separately
grouped = all_data.groupby('Ticker')

for ticker, df in grouped:
    # Ensure we're working with a copy of the dataframe
    df = df.copy()

    # Calculate the monthly average prices
    df.loc[:, 'Month'] = df['Date'].dt.to_period('M')
    monthly_avg = df.groupby('Month')['Close'].mean().reset_index()
    monthly_avg.rename(columns={'Close': 'Monthly_Avg_Close'}, inplace=True)

    # Calculate the monthly total volume
    monthly_volume_total = df.groupby('Month')['Volume'].sum().reset_index()
    monthly_volume_total.rename(columns={'Volume': 'Monthly_Volume_Total'}, inplace=True)

    # Calculate the monthly average volume
    monthly_volume_avg = df.groupby('Month')['Volume'].mean().reset_index()
    monthly_volume_avg.rename(columns={'Volume': 'Monthly_Volume_Avg'}, inplace=True)

    # Calculate the monthly volatility
    df.loc[:, 'Log_Return'] = df['Close'].pct_change().apply(lambda x: np.log(1 + x))
    monthly_volatility = df.groupby('Month')['Log_Return'].std().reset_index()

    # Calculate the number of months for volatility scaling
    num_months = len(monthly_volatility)
    if num_months > 0:
        monthly_volatility.loc[:, 'Monthly_Volatility'] = monthly_volatility['Log_Return'] * np.sqrt(num_months)
    else:
        monthly_volatility.loc[:, 'Monthly_Volatility'] = np.nan  # In case of no data

    monthly_volatility.drop(columns=['Log_Return'], inplace=True)

    # Merge the monthly average, total volume, average volume, and volatility data
    result = pd.merge(monthly_avg, monthly_volume_total, on='Month', how='inner')
    result = pd.merge(result, monthly_volume_avg, on='Month', how='inner')
    result = pd.merge(result, monthly_volatility, on='Month', how='inner')
    result['Ticker'] = ticker

    # Rearrange columns to put 'Ticker' first
    column_order = ['Ticker'] + [col for col in result.columns if col != 'Ticker']
    result = result[column_order]

    # Append to the list of processed data
    processed_data.append(result)

# Check if there's any data to concatenate
if processed_data:
    # Concatenate all data into a single dataframe
    final_df = pd.concat(processed_data, ignore_index=True)

    # Save the final dataframe to a CSV file
    output_file = os.path.expanduser('~/Small-Cap-Scout/raw_data/processed_yahoo_data.csv')
    final_df.to_csv(output_file, index=False)
    print(f"Data processing complete. Results saved to {output_file}.")

    # Optionally, display the first few rows of the final DataFrame
    print("First 5 rows of the processed data:")
    print(final_df.head())
else:
    print("No data to concatenate. Please check your data and filters.")

Failed to get ticker 'CIDM' reason: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
[*********************100%***********************]  1 of 1 completed

1 Failed download:
['CIDM']: YFTzMissingError('$%ticker%: possibly delisted; no timezone found')
[*********************100%***********************]  1 of 1 completed

1 Failed download:
['CMKG']: YFPricesMissingError('$%ticker%: possibly delisted; no price data found  (1d 2017-01-01 -> 2024-09-04)')
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

1 Failed download:
['ONEM']: YFTzMissingError('$%ticker%: possibly delisted; no timezone found')
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 

Data has been saved to /Users/eoingaynard/Small-Cap-Scout/raw_data/yahoo_stock_data_since_01_nov_2017.csv, BAAAAAM!


In [ ]:
all_data.head()

In [ ]:
all_data.tail()

In [ ]:
all_data.shape

In [ ]:
count_true = all_data.isna().any(axis=1).sum()
count_true

In [ ]:
# Save the combined dataframe to a new CSV file
output_file = os.path.join(data_directory, 'yahoo_stock_data_since_01_nov_2017.csv')
all_data.to_csv(output_file, index=False)

print(f"Data has been saved to {output_file}, BAAAAAM!")

## Get the monthly averages and volatility

In [7]:
all_data = pd.read_csv('~/Small-Cap-Scout/raw_data/yahoo_stock_data_since_01_nov_2017.csv', parse_dates=['Date'])

# Ensure the 'Date' column is in datetime format
all_data['Date'] = pd.to_datetime(all_data['Date'])

# Define the date range (modify as needed)
start_date = '2017-01-01'
end_date = datetime.today()

# Filter the data by the specified date range
all_data = all_data[(all_data['Date'] >= start_date) & (all_data['Date'] <= end_date)]

# Initialize a list to hold the processed data
processed_data = []

# Loop through each unique ticker in the data
for ticker in all_data['Ticker'].unique():
    # Filter the data for the current ticker
    df = all_data[all_data['Ticker'] == ticker]

    # Ensure the dataframe is not empty after filtering
    if not df.empty:
        # Calculate the monthly average prices
        df['Month'] = df['Date'].dt.to_period('M')
        monthly_avg = df.groupby('Month')['Close'].mean().reset_index()
        monthly_avg.rename(columns={'Close': 'Monthly_Avg_Close'}, inplace=True)

        # Calculate the monthly total volume
        monthly_volume_total = df.groupby('Month')['Volume'].sum().reset_index()
        monthly_volume_total.rename(columns={'Volume': 'Monthly_Volume_Total'}, inplace=True)

        # Calculate the monthly average volume
        monthly_volume_avg = df.groupby('Month')['Volume'].mean().reset_index()
        monthly_volume_avg.rename(columns={'Volume': 'Monthly_Volume_Avg'}, inplace=True)

        # Calculate the monthly volatility
        df['Log_Return'] = df['Close'].pct_change().apply(lambda x: np.log(1 + x))
        monthly_volatility = df.groupby('Month')['Log_Return'].std().reset_index()

        # Dynamically calculate the number of months for volatility scaling
        num_months = len(monthly_volatility)
        if num_months > 0:
            monthly_volatility['Monthly_Volatility'] = monthly_volatility['Log_Return'] * np.sqrt(num_months)
        else:
            monthly_volatility['Monthly_Volatility'] = np.nan  # In case of no data

        monthly_volatility.drop(columns=['Log_Return'], inplace=True)

        # Merge the monthly average, total volume, average volume, and volatility data
        result = pd.merge(monthly_avg, monthly_volume_total, on='Month', how='inner')
        result = pd.merge(result, monthly_volume_avg, on='Month', how='inner')
        result = pd.merge(result, monthly_volatility, on='Month', how='inner')
        result['Ticker'] = ticker

        # Rearrange columns to put 'Ticker' first
        column_order = ['Ticker'] + [col for col in result.columns if col != 'Ticker']
        result = result[column_order]

        # Append the result to the list
        processed_data.append(result)

# Check if there's any data to concatenate
if processed_data:
    # Concatenate all data into a single dataframe
    final_df = pd.concat(processed_data, ignore_index=True)

    # Save the final dataframe to a CSV file
    output_file = os.path.expanduser('~/Small-Cap-Scout/raw_data/processed_yahoo_data.csv')
    final_df.to_csv(output_file, index=False)
    print(f"Data processing complete. Results saved to {output_file}. WHOOP WHOOP!")

    # Optionally, display the first few rows of the final DataFrame
    print("First 5 rows of the processed data:")
    print(final_df.head())
else:
    print("No data to process. Please check your files and filters, por favor.")

# Load the processed data into a DataFrame to inspect
processed_df = pd.read_csv(output_file)

# Display the last 5 rows of the DataFrame
print(processed_df.tail())

/var/folders/5v/ww2jmqbx5nl0d2wfs2h4jnvc0000gn/T/ipykernel_39741/391004483.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Month'] = df['Date'].dt.to_period('M')
/var/folders/5v/ww2jmqbx5nl0d2wfs2h4jnvc0000gn/T/ipykernel_39741/391004483.py:37: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Log_Return'] = df['Close'].pct_change().apply(lambda x: np.log(1 + x))
/var/folders/5v/ww2jmqbx5nl0d2wfs2h4jnvc0000gn/T/ipykernel_39741/391004483.py:24: SettingWithCopyWarning: 
A value is trying to be set on 

Data processing complete. Results saved to /Users/eoingaynard/Small-Cap-Scout/raw_data/processed_yahoo_data.csv. WHOOP WHOOP!
First 5 rows of the processed data:
  Ticker    Month  Monthly_Avg_Close  Monthly_Volume_Total  \
0    TXG  2019-09          55.340769            14129700.0   
1    TXG  2019-10          52.053043             5148300.0   
2    TXG  2019-11          61.059001             3629400.0   
3    TXG  2019-12          68.063333             6148300.0   
4    TXG  2020-01          86.895238             5064700.0   

   Monthly_Volume_Avg  Monthly_Volatility  
0        1.086900e+06            0.387925  
1        2.238391e+05            0.323401  
2        1.814700e+05            0.329615  
3        2.927762e+05            0.489293  
4        2.411762e+05            0.288758  
       Ticker    Month  Monthly_Avg_Close  Monthly_Volume_Total  \
220365   ZVSA  2024-05           4.987591             2856500.0   
220366   ZVSA  2024-06           4.487737             1184000.0   
